In [1]:
%%time
import dask

CPU times: total: 125 ms
Wall time: 143 ms


In [2]:
dask.config.set(temporary_directory=r'D:\PATSTAT\dask_temp')

In [3]:
dask.config.set({'temporary_directory': r'D:\PATSTAT\dask_temp'})

In [4]:
dask.config.config

{'temporary-directory': 'D:\\PATSTAT\\dask_temp',
 'visualization': {'engine': None},
 'tokenize': {'ensure-deterministic': False},
 'dataframe': {'backend': 'pandas',
  'shuffle': {'method': None, 'compression': None},
  'parquet': {'metadata-task-size-local': 512, 'metadata-task-size-remote': 1},
  'dtype_backend': 'pandas',
  'convert_string': False},
 'array': {'backend': 'numpy',
  'rechunk': {'method': 'tasks'},
  'svg': {'size': 120},
  'slicing': {'split-large-chunks': None}},
 'optimization': {'annotations': {'fuse': True},
  'fuse': {'active': None,
   'ave-width': 1,
   'max-width': None,
   'max-height': inf,
   'max-depth-new-edges': None,
   'subgraphs': None,
   'rename-keys': True}}}

In [5]:
import dask.dataframe as dd


In [6]:
import os
print(os.getcwd())  # Prints the current working directory

workdir_path=r"D:\PATSTAT"
os.chdir(workdir_path)
print(os.getcwd())

C:\Users\radvanyi\PycharmProjects\ZSI_analytics\PATSTAT
D:\PATSTAT


In [7]:
%%time
tls_201 = dd.read_csv("table_tls201.csv", low_memory=False,dtype={'appln_nr': 'object',
       'appln_nr_original': 'object'})
tls_201.to_parquet("tls_201.parquet")

tls_206 = dd.read_csv("table_tls206.csv", low_memory=False)
tls_206.to_parquet("tls_206.parquet")

tls_207 = dd.read_csv("table_tls207.csv", low_memory=False)
tls_207.to_parquet("tls_207.parquet")

tls_204 = dd.read_csv("table_tls204.csv", low_memory=False)
tls_207.to_parquet("tls_204.parquet")

CPU times: total: 41min 20s
Wall time: 18min 32s


In [11]:
#Application data
tls_201_p = dd.read_parquet("tls_201.parquet")
tls_201_p.head()

appln_id appln_auth  appln_nr appln_kind appln_filing_date   
0         0         XX      None         D         9999-12-31  \
1         1         EP  103094.0         A         2000-02-15   
2         2         EP  107845.0         A         1992-12-02   
3         3         EP  202556.0         A         2000-07-17   
4         4         EP  300208.0         A         2000-01-13   

   appln_filing_year appln_nr_original ipr_type receiving_office   
0               9999              None       PI                   \
1               2000          00103094       PI                    
2               1992          00107845       PI                    
3               2000          00202556       PI                    
4               2000          00300208       PI                    

   internat_appln_id  ... earliest_publn_date earliest_publn_year   
0                  0  ...          9999-12-31                9999  \
1                  0  ...          2000-09-20                2000   
2                  0  ...          2000-08-02                2000   
3                  0  ...          2001-01-24                2001   
4                  0  ...          2000-07-26                2000   

  earliest_pat_publn_id granted  docdb_family_id  inpadoc_family_id   
0                     0       N                0                  0  \
1             293253293       Y          8554171                  1   
2             301548848       Y         27517085                  2   
3             291964096       N          7915918                  3   
4             292901055       Y         22889365                  4   

  docdb_family_size  nb_citing_docdb_fam  nb_applicants nb_inventors  
0                 1                    0              0            0  
1                 6                   79              1            4  
2                 8                   60              2            6  
3                 4                   22              2            3  
4                 6                   27              1            2  

[5 rows x 26 columns]

In [ ]:
# tls_201_p[((tls_201_p["appln_filing_year"]>2011)&
#            (tls_201_p["appln_filing_year"]<2024)&
#            (tls_201_p["granted"]=="Y"))]["appln_id"].nunique().compute()

In [ ]:
# tls_201_p[((tls_201_p["appln_filing_year"]>2011)&
#            (tls_201_p["appln_filing_year"]<2024)&
#            (tls_201_p["granted"]=="N"))]["appln_id"].nunique().compute()

In [12]:
tls_206_p = dd.read_parquet("tls_206.parquet",columns=["person_id","person_name","person_ctry_code"])
tls_206_p.head()

person_id        person_name person_ctry_code
0          1  Nokia Corporation               FI
1          2   Lipponen, Markku               FI
2          3     Laitinen, Timo               FI
3          4           Aho, Ari               FI
4          5    Knuutila, Jarno               FI

In [13]:
tls_207_p = dd.read_parquet("tls_207.parquet",columns=["person_id","appln_id"])
tls_207_p.head()

person_id  appln_id
0          1         1
1          1         7
2          1        46
3          1       775
4          1      1192

In [ ]:
# tls_207_p[tls_207_p["appln_id"]==1].compute()

In [14]:
tls_801 = dd.read_csv("table_tls801.csv", low_memory=False)
tls_801.head()

ctry_code iso_alpha3              st3_name organisation_flag      continent   
0        AD        AND               Andorra                           Europe  \
1        AE        ARE  United Arab Emirates                             Asia   
2        AF        AFG           Afghanistan                             Asia   
3        AG        ATG   Antigua and Barbuda                    North America   
4        AI        AIA              Anguilla                    North America   

  eu_member epo_member oecd_member discontinued  
0                                                
1                                                
2                                                
3                                                
4

In [15]:
china_df = tls_801[((tls_801.st3_name.str.lower().str.contains("china"))&
                    ~(tls_801.st3_name.str.lower().str.contains("taiwan")))].compute()
china_df

ctry_code iso_alpha3          st3_name organisation_flag continent   
46         CN        CHN             China                        Asia  \
96         HK        HKG  Hong Kong, China                        Asia   
146        MO        MAC      Macao, China                        Asia   

    eu_member epo_member oecd_member discontinued  
46                                                 
96                                                 
146

In [16]:
eu_df = tls_801[tls_801.eu_member=="Y"].compute()
eu_df

ctry_code iso_alpha3     st3_name organisation_flag continent eu_member   
11         AT        AUT      Austria                      Europe         Y  \
18         BE        BEL      Belgium                      Europe         Y   
20         BG        BGR     Bulgaria                      Europe         Y   
53         CY        CYP       Cyprus                      Europe         Y   
54         CZ        CZE      Czechia                      Europe         Y   
56         DE        DEU      Germany                      Europe         Y   
58         DK        DNK      Denmark                      Europe         Y   
65         EE        EST      Estonia                      Europe         Y   
71         ES        ESP        Spain                      Europe         Y   
74         FI        FIN      Finland                      Europe         Y   
78         FR        FRA       France                      Europe         Y   
91         GR        GRC       Greece                      Europe         Y   
98         HR        HRV      Croatia                      Europe         Y   
100        HU        HUN      Hungary                      Europe         Y   
103        IE        IRL      Ireland                      Europe         Y   
110        IT        ITA        Italy                      Europe         Y   
133        LT        LTU    Lithuania                      Europe         Y   
134        LU        LUX   Luxembourg                      Europe         Y   
135        LV        LVA       Latvia                      Europe         Y   
150        MT        MLT        Malta                      Europe         Y   
161        NL        NLD  Netherlands                      Europe         Y   
173        PL        POL       Poland                      Europe         Y   
174        PT        PRT     Portugal                      Europe         Y   
179        RO        ROU      Romania                      Europe         Y   
187        SE        SWE       Sweden                      Europe         Y   
190        SI        SVN     Slovenia                      Europe         Y   
191        SK        SVK     Slovakia                      Europe         Y   

    epo_member oecd_member discontinued  
11           Y           Y               
18           Y           Y               
20           Y                           
53           Y                           
54           Y           Y               
56           Y           Y               
58           Y           Y               
65           Y           Y               
71           Y           Y               
74           Y           Y               
78           Y           Y               
91           Y           Y               
98           Y                           
100          Y           Y               
103          Y           Y               
110          Y           Y               
133          Y           Y               
134          Y           Y               
135          Y           Y               
150          Y                           
161          Y           Y               
173          Y           Y               
174          Y           Y               
179          Y                           
187          Y           Y               
190          Y           Y               
191          Y           Y

In [19]:
western_df = tls_801[((tls_801.eu_member=="Y")|
                      (tls_801.ctry_code == 'US')|
                      (tls_801.ctry_code == 'NO')|
                      (tls_801.ctry_code == 'CH')|
                      (tls_801.ctry_code == 'UK'))].compute()
western_df

ctry_code iso_alpha3                  st3_name organisation_flag   
11         AT        AUT                   Austria                    \
18         BE        BEL                   Belgium                     
20         BG        BGR                  Bulgaria                     
41         CH        CHE               Switzerland                     
53         CY        CYP                    Cyprus                     
54         CZ        CZE                   Czechia                     
56         DE        DEU                   Germany                     
58         DK        DNK                   Denmark                     
65         EE        EST                   Estonia                     
71         ES        ESP                     Spain                     
74         FI        FIN                   Finland                     
78         FR        FRA                    France                     
91         GR        GRC                    Greece                     
98         HR        HRV                   Croatia                     
100        HU        HUN                   Hungary                     
103        IE        IRL                   Ireland                     
110        IT        ITA                     Italy                     
133        LT        LTU                 Lithuania                     
134        LU        LUX                Luxembourg                     
135        LV        LVA                    Latvia                     
150        MT        MLT                     Malta                     
161        NL        NLD               Netherlands                     
162        NO        NOR                    Norway                     
173        PL        POL                    Poland                     
174        PT        PRT                  Portugal                     
179        RO        ROU                   Romania                     
187        SE        SWE                    Sweden                     
190        SI        SVN                  Slovenia                     
191        SK        SVK                  Slovakia                     
220        US        USA  United States of America                     

         continent eu_member epo_member oecd_member discontinued  
11          Europe         Y          Y           Y               
18          Europe         Y          Y           Y               
20          Europe         Y          Y                           
41          Europe                    Y           Y               
53          Europe         Y          Y                           
54          Europe         Y          Y           Y               
56          Europe         Y          Y           Y               
58          Europe         Y          Y           Y               
65          Europe         Y          Y           Y               
71          Europe         Y          Y           Y               
74          Europe         Y          Y           Y               
78          Europe         Y          Y           Y               
91          Europe         Y          Y           Y               
98          Europe         Y          Y                           
100         Europe         Y          Y           Y               
103         Europe         Y          Y           Y               
110         Europe         Y          Y           Y               
133         Europe         Y          Y           Y               
134         Europe         Y          Y           Y               
135         Europe         Y          Y           Y               
150         Europe         Y          Y                           
161         Europe         Y          Y           Y               
162         Europe                    Y           Y               
173         Europe         Y          Y           Y               
174         Europe         Y          Y           Y               
179         Europe         Y 

In [29]:
ctry_list=list(china_df["ctry_code"])+list(western_df["ctry_code"])
ctry_list

['CN',
 'HK',
 'MO',
 'AT',
 'BE',
 'BG',
 'CH',
 'CY',
 'CZ',
 'DE',
 'DK',
 'EE',
 'ES',
 'FI',
 'FR',
 'GR',
 'HR',
 'HU',
 'IE',
 'IT',
 'LT',
 'LU',
 'LV',
 'MT',
 'NL',
 'NO',
 'PL',
 'PT',
 'RO',
 'SE',
 'SI',
 'SK',
 'US']

In [21]:
%%time
tls_appln_interval = tls_201_p[((tls_201_p["appln_filing_year"]>2010)&
                                (tls_201_p["appln_filing_year"]<2025))]["appln_id"].unique()

CPU times: total: 15.6 ms
Wall time: 6 ms


In [22]:
tls_206_p_subgroup = tls_206_p[tls_206_p["person_ctry_code"].isin(ctry_list)][["person_id","person_ctry_code"]]

In [33]:
%%time
appln_pers = (tls_207_p[tls_207_p['appln_id'].isin(tls_appln_interval.compute())]
             ).merge(
    tls_206_p_subgroup,
    on="person_id",how="inner")[["appln_id","person_id","person_ctry_code"]].drop_duplicates()

appln_pers = appln_pers[appln_pers["person_ctry_code"].isin(ctry_list)].drop_duplicates()
appln_pers.to_parquet("appln_pers.parquet")

CPU times: total: 45min 6s
Wall time: 11min 58s


In [24]:
appln_pers.columns

Index(['appln_id', 'person_id', 'person_ctry_code'], dtype='object')

In [32]:
appln_pers.shape

(Delayed('int-8f92fe68-e5a1-4f9e-a30c-77833e0fff26'), 3)

In [34]:
appln_pers["appln_id"].nunique().compute()

KeyboardInterrupt: 

In [35]:
id_selector = dd.read_parquet("appln_pers.parquet")

In [36]:
id_selector.head()

appln_id  person_id person_ctry_code
0  515465980   76083836               CH
1  530145641   76089672               AT
2  532157050   76089962               CN
3  532162718   76089962               CN
4  532164120   76089962               CN

In [50]:
id_selector.person_ctry_code.nunique().compute()

33

In [52]:
id_selector.person_ctry_code.value_counts().compute()

person_ctry_code
US    16249179
DE     4980374
CN     4137237
FR     1953182
CH      819720
NL      712685
IT      659643
SE      575791
ES      404734
AT      341489
BE      324202
FI      308472
DK      267490
PL      256066
NO      134220
IE      123974
CZ      120706
HU       55884
HK       51785
RO       49656
PT       44892
LU       39736
GR       29126
SK       28316
SI       27382
BG       13125
LV       10131
EE        9364
LT        8910
HR        6540
CY        6232
MT        6021
MO        1703
Name: count, dtype: int64

In [53]:
%%time
eu_id = id_selector[id_selector["person_ctry_code"].isin(list(western_df["ctry_code"]))]["appln_id"].unique()
china_id = id_selector[id_selector["person_ctry_code"].isin(list(china_df["ctry_code"]))]["appln_id"].unique()
                                                         
common_id = id_selector[id_selector["appln_id"].isin(eu_id.compute())&
                        id_selector["appln_id"].isin(china_id.compute())]

common_id.to_parquet("common_id_CHEU.parquet")

CPU times: total: 29.2 s
Wall time: 29.6 s


In [54]:
%%time
common_id["appln_id"].nunique().compute()

CPU times: total: 5.62 s
Wall time: 5.61 s


203873

In [55]:
filtered_ids = dd.read_parquet("common_id_CHEU.parquet")

In [56]:
filtered_ids.head()

appln_id  person_id person_ctry_code
102  531966031   76189975               CN
104  533342168   76190204               CN
117  504910639   76196951               DE
144  537370384   76217739               AT
160  527648360   76227149               ES

In [57]:
filtered_ids.sort_values(by="appln_id").compute()

appln_id  person_id person_ctry_code
9469    330225325     429997               CN
16032   330225325    4555802               DE
4448    330225397    4849499               US
19897   330225397      60435               US
31709   330225397       4284               US
...           ...        ...              ...
69073   587679340   18114863               US
74083   587679340   19330879               CN
102624  587679340   53002958               US
73989   587679340   41556280               US
101114  587679340   48821759               US

[1025221 rows x 3 columns]

In [58]:
%%time
id_scope=filtered_ids["appln_id"].unique().compute()
pers_id_scope=filtered_ids["person_id"].unique().compute()

CPU times: total: 234 ms
Wall time: 216 ms


In [59]:
# tls_201_p.head()

In [60]:
outdir = "WESTERN_CH_scope"
os.makedirs(outdir, exist_ok=True)

In [61]:
%%time
#Application data
tls_201_p = dd.read_parquet("tls_201.parquet")
tls_201_scope = tls_201_p[tls_201_p['appln_id'].isin(id_scope)]
tls_201_scope.compute().to_csv(f"{outdir}/tls_201_scope.csv", index=False)

CPU times: total: 4min 42s
Wall time: 2min 58s


In [62]:
%%time
#Person-appln data
tls_207_p = dd.read_parquet("tls_207.parquet")
tls_207_scope = tls_207_p[((tls_207_p['person_id'].isin(pers_id_scope))&
                           (tls_207_p['appln_id'].isin(id_scope)))]
tls_207_scope.compute().to_csv(f"{outdir}/tls_207_scope.csv",index=False)

CPU times: total: 1min 46s
Wall time: 31.4 s


In [63]:
%%time
#Person data
tls_206_p = dd.read_parquet("tls_206.parquet")
tls_206_scope = tls_206_p[tls_206_p['person_id'].isin(pers_id_scope)]
tls_206_scope.compute().to_csv(f"{outdir}/tls_206_scope.csv",index=False)

CPU times: total: 4min 59s
Wall time: 3min 38s


In [64]:
%%time
#Application title data
tls_202_p = dd.read_csv("table_tls202.csv")
tls_202_scope = tls_202_p[tls_202_p['appln_id'].isin(id_scope)]
tls_202_scope.compute().to_csv(f"{outdir}/tls_202_scope.csv", index=False)

CPU times: total: 2min 49s
Wall time: 2min 6s


In [65]:
%%time
#IPC data
tls_224_p = dd.read_csv("table_tls224.csv")
tls_224_p_scope = tls_224_p[tls_224_p['appln_id'].isin(id_scope)]
tls_224_p_scope.compute().to_csv(f"{outdir}/tls_224_scope.csv", index=False)

CPU times: total: 3min 17s
Wall time: 2min 1s
